# Workshop - Topic modeling

## Tweet เกี่ยวกับอะไรบ้าง

In [1]:
!curl -O https://raw.githubusercontent.com/attapol/programming-nlp-book/main/book/module7/data/tweet_tokenized.csv

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 16.3M  100 16.3M    0     0  3840k      0  0:00:04  0:00:04 --:--:-- 4041k    0


In [2]:
import pandas as pd
data_tokenized = pd.read_csv('tweet_tokenized.csv')
docs = [x.split('|') for x in data_tokenized.tokens]

In [3]:
docs[0]

['กกต.',
 'จี้“',
 'อนาคต',
 'ใหม่”',
 'แจง',
 'เงิน',
 'กู้',
 '“',
 'ธนาธร”',
 ' https',
 '://t.co/iKuv86oaK8']

In [4]:
!pip install gensim

In [5]:
!pip install pythainlp

In [6]:
from gensim.models.ldamodel import LdaModel
from gensim import corpora
from collections import Counter
from pythainlp.corpus import thai_stopwords

In [7]:
import re
patt = re.compile('^[ก-์]+$')
new_doc_list = []
all_words = []
for doc in docs:
    new_doc = []
    for w in doc:
        if w not in thai_stopwords() and patt.match(w):
            new_doc.append(w)
            all_words.append(w)
    new_doc_list.append(new_doc)
    

In [8]:
c = Counter(all_words)

In [9]:
c.most_common(100)

[('คน', 2726),
 ('ทหาร', 2308),
 ('ทำ', 2097),
 ('ดี', 1695),
 ('ประชาชน', 1619),
 ('กองทัพบก', 1375),
 ('ไทย', 1222),
 ('กำลังใจ', 1057),
 ('พรรค', 946),
 ('เรื่อง', 923),
 ('อนาคต', 867),
 ('งาน', 857),
 ('ข่าว', 833),
 ('ตัว', 804),
 ('น้ำ', 719),
 ('ชีวิต', 705),
 ('ไฟ', 669),
 ('ช่วยเหลือ', 664),
 ('ท่าน', 648),
 ('พื้นที่', 633),
 ('ไวรัส', 614),
 ('ยิง', 597),
 ('ภัย', 587),
 ('พล', 585),
 ('รู้', 583),
 ('ฝึก', 577),
 ('อย่า', 576),
 ('ผม', 557),
 ('สร้าง', 542),
 ('ดู', 537),
 ('ปี', 529),
 ('กอง', 515),
 ('ติด', 510),
 ('ยุบ', 509),
 ('ประเทศ', 508),
 ('บ้าน', 494),
 ('หน่วย', 483),
 ('ป่า', 470),
 ('เวลา', 467),
 ('ปัญหา', 466),
 ('โคราช', 460),
 ('ป้องกัน', 447),
 ('เงิน', 430),
 ('เหตุการณ์', 428),
 ('สู้', 424),
 ('ชาติ', 416),
 ('เชื้อ', 416),
 ('หน้า', 414),
 ('ดับ', 404),
 ('กราด', 401),
 ('เจ้าหน้าที่', 397),
 ('ทัพ', 396),
 ('เสียใจ', 388),
 ('รัฐบาล', 386),
 ('รถ', 386),
 ('ยอด', 379),
 ('รอ', 379),
 ('ครอบครัว', 362),
 ('เมือง', 354),
 ('ขอบคุณ', 347),
 ('เยี่ยม', 

## Train LDA 
Assume ว่าข้อมูลอยู่ในรูป list of list of words แล้ว

In [10]:
import re
patt = re.compile('^[ก-์]+$')
custom_stop = {'RT', 'https'}
doc_list_lda = []
for doc in docs:
    new_doc = []
    for w in doc:
        if w not in thai_stopwords() and patt.match(w) and w not in custom_stop:
            new_doc.append(w)
            all_words.append(w)
    doc_list_lda.append(new_doc)
    
lda_dict = corpora.Dictionary(doc_list_lda)
data_set = []
for doc in doc_list_lda:
    data_set.append(lda_dict.doc2bow(doc))
model = LdaModel(corpus=data_set, num_topics=10, id2word=lda_dict, 
                 alpha='auto', eval_every=10, random_state=10)

## Topic-keys

In [11]:
model.show_topic(0)

[('กองทัพบก', 0.09621996),
 ('ประชาชน', 0.04953569),
 ('ยอด', 0.03530424),
 ('ปัญหา', 0.027296925),
 ('ฝุ่น', 0.024649872),
 ('ห่วงใย', 0.024357473),
 ('หน้ากาก', 0.018926686),
 ('ชาติ', 0.018856036),
 ('อนามัย', 0.018278295),
 ('เพื่อประชาชน', 0.017611608)]

In [12]:
for i in range(model.num_topics):
    print (str(i) + ':' + ' '.join([w[0] for w in model.show_topic(i)]))

0:กองทัพบก ประชาชน ยอด ปัญหา ฝุ่น ห่วงใย หน้ากาก ชาติ อนามัย เพื่อประชาชน
1:น้ำ คน พื้นที่ รถ ทำ ดี พล ประเทศ ภัย แล้ง
2:ทำ ดี คน เจ้าหน้าที่ ขอบคุณ ทหาร งาน รู้ ตัว เรื่อง
3:โคราช ช่วยเหลือ ยิง ชีวิต กราด กอง แจก ทัพ ทหาร บริจาค
4:ไทย เสียใจ คน ฝึก กองทัพบก ครอบครัว ปี หน่วย รอง ชีวิต
5:พรรค อนาคต ยุบ เรื่อง ข่าว โดน ทำ ผม ติดตาม เมือง
6:ไวรัส สู้ ทหาร คน ภัย ปลอด ไทย แดน ชาย บัญชา
7:กำลังใจ ท่าน ทหาร ชื่นชม พระราชทาน ยอด ฝึก ชุด พี่ สู้
8:พระเจริญ ทหาร บิน ประชาชน พระองค์ ที่พึ่ง เช้า อากาศ เรือ สื่อ
9:ไฟ ป่า ประชาชน ทหาร ดับ ดี ป้องกัน เงิน รอ อย่า


In [13]:
!pip install pyldavis

  Using cached pyLDAvis-3.3.1.tar.gz (1.7 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
  Using cached funcy-1.17-py2.py3-none-any.whl (33 kB)
  Created wheel for pyldavis: filename=pyLDAvis-3.3.1-py2.py3-none-any.whl size=136882 sha256=4339d30f2bdaba8e963885e90362b1da4783d4c4433d55003f129b2ba04fb736
  Stored in directory: /Users/te/Library/Caches/pip/wheels/57/a4/86/d10c6c2e0bf149fbc0afb0aa5a6528ac35b30a133a0270c477
  Created wheel for sklearn: filename=sklearn-0.0-py2.py3-none-any.whl size=1310 sha256=ccd70299e17df2942f111afa892db54d6d8e16693b3e687b72b97ffb54537f9a
  Stored in directory: /Users/te/Library/Caches/pip/wheels/e4/7b/98/b6466d71b8d738a0c547008b9eb39bf8676d1ff6ca4b22af1c
Successfully built pyldavis sklearn


In [14]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()

In [18]:
vis = gensimvis.prepare(model, data_set, lda_dict)
vis

/opt/anaconda3/lib/python3.9/site-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.169577 -0.024358       1        1  15.159561
9     -0.032482  0.074254       2        1  12.276992
5     -0.207101  0.179745       3        1  11.953122
4      0.060698 -0.109993       4        1  11.329514
6     -0.033364 -0.108209       5        1   9.969722
1     -0.104789 -0.041057       6        1   9.323101
3      0.196635 -0.090760       7        1   8.101690
0      0.176032  0.187507       8        1   7.522877
7     -0.013068 -0.197283       9        1   7.463598
8      0.127016  0.130155      10        1   6.899822, topic_info=            Term         Freq        Total Category  logprob  loglift
40       กำลังใจ  1701.000000  1701.000000  Default  30.0000  30.0000
69      กองทัพบก  1605.000000  1605.000000  Default  29.0000  29.0000
45            ทำ  2434.000000  2434.000000  Default  28.0000  28.0000
1          อนาคต   975.000000   975.000000  Default  27.0000  27.0000
87          พรรค  1020.000000  1020.000000  Default  26.0000  26.0000
..           ...          ...          ...      ...      ...      ...
662        โอกาส   114.477731   359.087082  Topic10  -4.5108   1.5305
225  ประชาธิปไตย    80.028568   143.952918  Topic10  -4.8688   2.0866
89           หาย    79.006852   196.017338  Topic10  -4.8817   1.7650
969        หน่วย    84.078772   567.937008  Topic10  -4.8194   0.7634
49            คน    92.856763  2956.703663  Topic10  -4.7201  -0.7871

[622 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
700       3  0.990861         ก
142       2  0.984107    กฏหมาย
869       1  0.217972      กรณี
869       9  0.771287      กรณี
1352      2  0.984492   กรมทหาร
...     ...       ...       ...
84        5  0.935635     ไวรัส
703       3  0.962183  ไว้วางใจ
703       6  0.032073  ไว้วางใจ
91        2  0.979194      ไหม้
3213      2  0.980512      ไอซ์

[1417 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 10, 6, 5, 7, 2, 4, 1, 8, 9])

## Doc-topic 

In [16]:
doc_topics = model.get_document_topics(data_set)

In [17]:
def print_doc_for_topic(doc_topics, doc_list_lda, topic_no):
    printed = set()
    for i in range(len(doc_list_lda)):
        top_topic, top_proportion = doc_topics[i][0]
        if top_topic == topic_no and top_proportion > 0.5:
            to_print = ''.join(doc_list_lda[i])
            if to_print not in printed:
                print (to_print)
                print ('------')
            printed.add(to_print)
            #doc_topics[0]
print_doc_for_topic(doc_topics, docs, 2)

RT @MaisonWanvipa: ปี 2562 ขาดประชุม ส.ส.ไป 1 ครั้ง (ติดประเด็นเลิกจ้างคนงาน) ปีนี้มาลุยกันใหม่ 
#ทํางานวนไป #อนาคตใหม่ https://t.co/jRIbk2…
------
RT @MaisonWanvipa: มาเป็นองค์ประชุมตามเวลา ถึงแม้จะทำหน้าที่เรื่องงบประมาณไปครบถ้วนแล้ว นี่ถ้าเป็นเมื่อก่อนทำงานแล้ว #เสียบบัตรแทนกัน โดนเ…
------
ขอสรรเสริญในความกล้าของนาย ธีระ ฉัตรนิ่ม รปภ.ห้างที่เอาชีวิตเข้่าแลกวิ่งไปกดปิดประตูอัตโนมัติจนถูกคนร้ายยิงเสียชีวิต แต่ความกล้าหาญนั้นก็ไม่สูญเปล่าเพราะมันทำให้ตำรวจได้มาซึ่งพยานหลักฐานสำคัญที่สุด คือ เหงื่อของคนร้าย นำมาสู่การจับกุม คดีชิงทอง
------
จะไม่ยอมให้ใครย้ำยีแผ่นดินนี้ของเราไปได้ยอมเสียเลือดเสียเนื้อเสียกลายหากต้องเสียแผ่นดิน
จะรักษาแผ่นดินของพ่อตอบแทนคุณท่านทำให้เรามีกินประเทศสยามจะจำเนินไม่สิ้นแผ่นดินขวานทอง
------
28 ก.พ. 63  พล.รพศ.1 ได้จัดพิธีสักการะพระไพรีพินาศ พิธีบวงสรวง และพิธีทำบุญเพื่อเป็นสิริมงคลและอุทิศส่วนกุศลให้กับกำลังพลที่เสียชีวิต ของ พล.รพศ.1 มี ผบช.นขต.(ลพบุรี), แม่บ้าน พล.รพศ.1+ นขต., กำลังพลและครอบครัว เข้าร่วมพิธี โดยมี พล.ต.ชาตรี  กิตติขจร ผบ.พล.รพศ.1 เป็นประธา

## แบบฝึกหัด
### ข้อ 1
ลองเปลี่ยนจำนวน topic แล้วสังเกตุดูว่าผลเปลี่ยนไปบ้างมั้ย ยังได้ข้อสรุปเดิมอีกหรือไม่

### ข้อ 2

Train topic model จากไฟล์ `prachathai-news-sample-2000.txt` ซึ่งอยู่ในรูป one line per doc 
ก่อนอื่นเราจะต้องเปลี่ยนข้อมูลให้อยู่ในรูป list of (list of words) ก่อนและทำการ pre-processing โดยการ
1. word tokenize
2. เอา stopwords ออกไปก่อนให้เรียบร้อย 
3. เก็บเอาเฉพาะคำที่เป็นภาษาไทย ไม่เอาตัวเลข ไม่เอาภาษาอังกฤษ

ให้ copy code ข้างบนเพื่อเทรน LDA และวิเคราะห์ผลจาก topic keys ที่ได้ อาจจะต้องมีการปรับจำนวน topic ให้เหมาะสม